Installing packages

In [3]:
!pip install tpot
!pip install mljar-supervised
!pip install pandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 4.1 MB/s 
     |████████████████████████████████| 255.9 MB 43 kB/s 
     |████████████████████████████████| 139 kB 46.8 MB/s 
  Created wheel for stopit: filename=stopit-1.1.2-py3-none-any.whl size=11954 sha256=8b85dfe6b33c58e7aa62879bfba64688a25bcb28061c55b7d8a60ff885ce0cc6
  Stored in directory: /root/.cache/pip/wheels/e2/d2/79/eaf81edb391e27c87f51b8ef901ecc85a5363dc96b8b8d71e3
Successfully built stopit
  Attempting uninstall: xgboost
    Found existing installation: xgboost 0.90
    Uninstalling xgboost-0.90:
      Successfully uninstalled xgboost-0.90
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 112 kB 6.1 MB/s 
     |████████████████████████████████| 2.0 MB 48.4 MB/s 
     |████████████████████████████████| 76.6 MB 142 kB/s 
     |███████████████

In [4]:
import pandas as pd
import tpot as tp
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

Importing data

In [5]:
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [6]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

Determining possible important variables

In [7]:
sparcs['Length of Stay'].describe()

count     23583
unique       97
top           2
freq       5378
Name: Length of Stay, dtype: object

In [8]:
sparcs['Total Costs'].describe()

count    2.358300e+04
mean     1.472282e+04
std      2.718098e+04
min      6.700000e-01
25%      4.471700e+03
50%      8.320120e+03
75%      1.590874e+04
max      1.591541e+06
Name: Total Costs, dtype: float64

In [9]:
sparcs['APR Risk of Mortality'].value_counts()

Minor       13990
Moderate     4952
Major        3452
Extreme      1187
Name: APR Risk of Mortality, dtype: int64

# Developing a binary version of the sparcs data

In [10]:
sparcs['Length of Stay'] = pd.to_numeric(sparcs['Length of Stay'], errors='coerce')
sparcs['sparcs_los'] = sparcs['Length of Stay'].apply(lambda x: 'long' if x > 3 else 'short')
sparcs.drop('Length of Stay', axis=1, inplace=True)
sparcs['sparcs_los'].value_counts()


short    13008
long     10575
Name: sparcs_los, dtype: int64

Creating a binary classifier model 

In [11]:
X = sparcs.drop(columns=['sparcs_los'])
y = sparcs["sparcs_los"]

In [12]:
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2 Payment Typology 3  \
0      Private Health Insurance                       NaN                NaN   
1        Blue Cross/Blue Shield                  Self-Pay           Self-Pay   
2                      Self-Pay                  Self-Pay           Self-Pay   
3                      Medicare                  Medicare           Self-Pay   
4        Blue Cross/Blue Shield       

In [13]:
y

0        short
1        short
2        short
3        short
4         long
         ...  
23578     long
23579    short
23580     long
23581     long
23582     long
Name: sparcs_los, Length: 23583, dtype: object

In [14]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.25)


In [15]:
automl = AutoML(
    results_path="sparcs_binary_los",
    mode="Explain"
)

In [16]:
automl.fit(X_train, y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_binary_los
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.687821 trained in 0.65 seconds


2_DecisionTree logloss 0.436436 trained in 14.94 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.259062 trained in 24.71 seconds
4_Default_NeuralNetwork logloss 0.362407 trained in 8.78 seconds
5_Default_RandomForest logloss 0.380921 trained in 23.27 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.259062 trained in 1.62 seconds
AutoML fit time: 86.72 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='sparcs_binary_los')

In [17]:
pred = automl.predict(X_test)
pred

array(['short', 'long', 'long', ..., 'long', 'long', 'short'],
      dtype=object)

In [18]:
automl.report()

Testing new data

In [19]:
automl_sparcs_los = AutoML(results_path="sparcs_binary_los")


In [20]:
X_withlos = sparcs.sample(5)
X_withoutlos = X_withlos.drop(columns=['sparcs_los'])

In [21]:
predict = automl.predict(X_withoutlos)
predict

array(['long', 'long', 'long', 'short', 'long'], dtype=object)

In [22]:
values_actual = X_withlos['sparcs_los'].values.tolist()
values_predicted = predict.tolist()
output = pd.DataFrame({'actual': values_actual, 'predicted': values_predicted})
output

actual predicted
0   long      long
1   long      long
2   long      long
3  short     short
4   long      long

# Binary Classifier Example

In [23]:
heart = pd.read_csv('https://raw.githubusercontent.com/csanicola74/AutoML-examples/main/data/heart.csv')
heart

age  sex  cp  trtbps  chol  fbs  restecg  thalachh  exng  oldpeak  slp  \
0     63    1   3     145   233    1        0       150     0      2.3    0   
1     37    1   2     130   250    0        1       187     0      3.5    0   
2     41    0   1     130   204    0        0       172     0      1.4    2   
3     56    1   1     120   236    0        1       178     0      0.8    2   
4     57    0   0     120   354    0        1       163     1      0.6    2   
..   ...  ...  ..     ...   ...  ...      ...       ...   ...      ...  ...   
298   57    0   0     140   241    0        1       123     1      0.2    1   
299   45    1   3     110   264    0        1       132     0      1.2    1   
300   68    1   0     144   193    1        1       141     0      3.4    1   
301   57    1   0     130   131    0        1       115     1      1.2    1   
302   57    0   1     130   236    0        0       174     0      0.0    1   

     caa  thall  output  
0      0      1       1  
1      0      2       1  
2      0      2       1  
3      0      2       1  
4      0      2       1  
..   ...    ...     ...  
298    0      3       0  
299    0      3       0  
300    2      3       0  
301    1      3       0  
302    1      2       0  

[303 rows x 14 columns]

etc

In [24]:
heart.columns

Index(['age', 'sex', 'cp', 'trtbps', 'chol', 'fbs', 'restecg', 'thalachh',
       'exng', 'oldpeak', 'slp', 'caa', 'thall', 'output'],
      dtype='object')

In [32]:
heart['age'].describe()

count    303.000000
mean      54.366337
std        9.082101
min       29.000000
25%       47.500000
50%       55.000000
75%       61.000000
max       77.000000
Name: age, dtype: float64

In [33]:
heart['thalachh'].describe()

count    303.000000
mean     149.646865
std       22.905161
min       71.000000
25%      133.500000
50%      153.000000
75%      166.000000
max      202.000000
Name: thalachh, dtype: float64

In [34]:
heart['trtbps'].describe()

count    303.000000
mean     131.623762
std       17.538143
min       94.000000
25%      120.000000
50%      130.000000
75%      140.000000
max      200.000000
Name: trtbps, dtype: float64

In [35]:
heart['chol'].describe()

count    303.000000
mean     246.264026
std       51.830751
min      126.000000
25%      211.000000
50%      240.000000
75%      274.500000
max      564.000000
Name: chol, dtype: float64

In [36]:
X_without_chol = heart.drop(columns=['chol'])
y_chol = heart['chol']

In [37]:
X_without_chol

age  sex  cp  trtbps  fbs  restecg  thalachh  exng  oldpeak  slp  caa  \
0     63    1   3     145    1        0       150     0      2.3    0    0   
1     37    1   2     130    0        1       187     0      3.5    0    0   
2     41    0   1     130    0        0       172     0      1.4    2    0   
3     56    1   1     120    0        1       178     0      0.8    2    0   
4     57    0   0     120    0        1       163     1      0.6    2    0   
..   ...  ...  ..     ...  ...      ...       ...   ...      ...  ...  ...   
298   57    0   0     140    0        1       123     1      0.2    1    0   
299   45    1   3     110    0        1       132     0      1.2    1    0   
300   68    1   0     144    1        1       141     0      3.4    1    2   
301   57    1   0     130    0        1       115     1      1.2    1    1   
302   57    0   1     130    0        0       174     0      0.0    1    1   

     thall  output  
0        1       1  
1        2       1  
2        2       1  
3        2       1  
4        2       1  
..     ...     ...  
298      3       0  
299      3       0  
300      3       0  
301      3       0  
302      2       0  

[303 rows x 13 columns]

In [38]:
y_chol

0      233
1      250
2      204
3      236
4      354
      ... 
298    241
299    264
300    193
301    131
302    236
Name: chol, Length: 303, dtype: int64

In [39]:
automl_2 = AutoML()
automl_2.fit(X_without_chol,y_chol)

AutoML directory: AutoML_2
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Linear', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 3 models
1_Baseline rmse 40.458838 trained in 0.66 seconds
2_DecisionTree rmse 46.646306 trained in 11.47 seconds
3_Linear rmse 40.094017 trained in 2.92 seconds
* Step default_algorithms will try to check up to 3 models
4_Default_Xgboost rmse 43.4703 trained in 4.7 seconds
5_Default_NeuralNetwork rmse 36.975542 trained in 0.88 seconds
6_Default_RandomForest rmse 37.908018 trained in 8.57 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 36.759846 trained in 0.31 seconds
AutoML fit time: 37.93 seconds
AutoML best model: Ensemble


AutoML()

In [40]:
automl_2.report()

In [41]:
heart['reg_pred'] = automl_2.predict(X_without_chol)

In [42]:
print('reg_pred')
print(heart[['chol', 'reg_pred']].head())

reg_pred
   chol    reg_pred
0   233  242.030588
1   250  233.076180
2   204  256.958405
3   236  236.239116
4   354  253.012820


# Porting files to a .zip

In [43]:
!zip -r /content/download.zip /content/

  adding: content/ (stored 0%)
  adding: content/.config/ (stored 0%)
  adding: content/.config/.last_opt_in_prompt.yaml (stored 0%)
  adding: content/.config/.last_update_check.json (deflated 22%)
  adding: content/.config/gce (stored 0%)
  adding: content/.config/active_config (stored 0%)
  adding: content/.config/logs/ (stored 0%)
  adding: content/.config/logs/2022.11.09/ (stored 0%)
  adding: content/.config/logs/2022.11.09/14.28.33.298481.log (deflated 53%)
  adding: content/.config/logs/2022.11.09/14.29.37.145223.log (deflated 55%)
  adding: content/.config/logs/2022.11.09/14.29.12.473847.log (deflated 54%)
  adding: content/.config/logs/2022.11.09/14.28.03.059919.log (deflated 91%)
  adding: content/.config/logs/2022.11.09/14.29.37.960408.log (deflated 53%)
  adding: content/.config/logs/2022.11.09/14.28.57.244063.log (deflated 86%)
  adding: content/.config/configurations/ (stored 0%)
  adding: content/.config/configurations/config_default (deflated 15%)
  adding: content/.con

In [44]:
from google.colab import files
files.download('/content/download.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>